In [9]:
import os
import pandas as pd
import glob
import re

In [24]:
def combine_excel_files(directory_path, output_csv='combined_mcas_data.csv', output_parquet='combined_mcas_data.parquet'):
    """
    Combine all Excel files in a directory into a single dataset with proper headers.
    Converts to both CSV and Parquet formats.
    Handles data types: numbers for most fields, strings for District name, subject, district code and year.
    
    Parameters:
    directory_path (str): Path to the directory containing Excel files
    output_csv (str): Name of the output CSV file
    output_parquet (str): Name of the output Parquet file
    """
    # Get list of all Excel files in the directory
    all_files = glob.glob(os.path.join(directory_path, "*.xlsx"))
    
    # Create an empty list to store DataFrames
    dfs = []
    all_columns_sets = []
    
    # First pass - examine structure of the first file to identify headers
    if all_files:
        # Read the first few rows of the first file to inspect
        sample_df = pd.read_excel(all_files[0], header=None, nrows=10)
        print(f"Preview of first file ({all_files[0]}):")
        print(sample_df.head(10))
        
        # Find the actual header row by looking for rows where many columns have values
        non_empty_counts = sample_df.notna().sum(axis=1)
        potential_header_rows = non_empty_counts[non_empty_counts > 5].index.tolist()
        
        if potential_header_rows:
            header_row = potential_header_rows[1] if len(potential_header_rows) > 1 else potential_header_rows[0]
            # Use row index where we detect MCAS data pattern
            for i in potential_header_rows:
                if 'DISTRICT NAME' in str(sample_df.iloc[i].values).upper() or 'SCHOOL NAME' in str(sample_df.iloc[i].values).upper():
                    header_row = i
                    break
            print(f"Detected header row at index {header_row}: {sample_df.iloc[header_row].tolist()}")
        else:
            header_row = 0
            print("Could not detect header row, using first row")
    
    # Get the first file's column order as a reference
    first_file_columns = None
    
    # Loop through each Excel file
    for file in all_files:
        try:
            # Extract year from filename
            year_match = re.search(r'NextGenMCAS_(\d{4})\.xlsx', os.path.basename(file))
            if year_match:
                year = year_match.group(1)
            else:
                year = "Unknown"
            
            # Define columns that should be treated as strings
            string_cols = []
            
            # First check what columns exist in the file
            temp_df = pd.read_excel(file, header=header_row, nrows=0)
            for col in temp_df.columns:
                col_str = str(col).upper()
                if ('DISTRICT' in col_str and ('CODE' in col_str or 'ID' in col_str or 'NUMBER' in col_str)) or \
                   ('DISTRICT NAME' in col_str) or ('SUBJECT' in col_str):
                    string_cols.append(col)
            
            # Read the Excel file
            df = pd.read_excel(
                file, 
                header=header_row, 
                dtype={col: str for col in string_cols}  # Convert specified columns to string
            )
            
            # Clean column names
            df.columns = [col.strip().replace('\n', ' ') if isinstance(col, str) else str(col) for col in df.columns]
            
            # Store the first file's column order
            if first_file_columns is None:
                first_file_columns = df.columns.tolist()
            
            # Add year column as string
            df['Year'] = str(year)
            
            # Store the columns from this file
            all_columns_sets.append(set(df.columns))
            
            # Append to list
            dfs.append(df)
            print(f"Successfully processed: {file} (Year: {year})")
        except Exception as e:
            print(f"Error processing {file}: {e}")
    
    # Find common columns across all files (intersection of all column sets)
    if all_columns_sets:
        common_columns = set.intersection(*all_columns_sets)
        print(f"Common columns across all files: {common_columns}")
        
        # Ensure 'Year' is in common columns
        if 'Year' not in common_columns:
            common_columns.add('Year')
        
        # Keep only common columns in each DataFrame
        for i in range(len(dfs)):
            dfs[i] = dfs[i][list(common_columns)]
    
    # Combine all DataFrames
    if dfs:
        # Combine DataFrames with only the common columns
        combined_df = pd.concat(dfs, ignore_index=True)
        
        # Remove rows that are likely headers from other files
        possible_header_rows = []
        for col in common_columns:
            if col != 'Year':  # Skip checking Year column
                for i, row in combined_df.iterrows():
                    for val in row:
                        if isinstance(val, str) and col.lower() in str(val).lower():
                            possible_header_rows.append(i)
        
        # Remove duplicate header rows
        possible_header_rows = list(set(possible_header_rows))
        print(f"Removing {len(possible_header_rows)} possible header rows")
        combined_df = combined_df.drop(possible_header_rows, errors='ignore')
        
        # Identify string columns and numeric columns
        string_columns = []
        district_col = None
        district_code_col = None
        subject_col = None
        
        for col in combined_df.columns:
            col_upper = col.upper()
            if 'DISTRICT NAME' in col_upper:
                district_col = col
                string_columns.append(col)
            elif ('DISTRICT' in col_upper and ('CODE' in col_upper or 'ID' in col_upper or 'NUMBER' in col_upper)):
                district_code_col = col
                string_columns.append(col)
            elif 'SUBJECT' in col_upper:
                subject_col = col
                string_columns.append(col)
        
        # Add Year to string columns
        string_columns.append('Year')
        
        # Convert all other columns to numeric
        for col in combined_df.columns:
            if col not in string_columns:
                # Try to convert to numeric, replace errors with NaN
                combined_df[col] = pd.to_numeric(combined_df[col], errors='coerce')
        
        # Reorder columns to put DISTRICT NAME and Year first
        if district_col:
            # Create new column order with district_col and Year first, then others in original order
            remaining_cols = [col for col in combined_df.columns 
                             if col != district_col and col != 'Year']
            
            # Sort remaining columns based on their order in the first file
            if first_file_columns:
                # Get the indices of each column in the original order
                col_indices = {}
                for i, col in enumerate(first_file_columns):
                    if col in remaining_cols:
                        col_indices[col] = i
                
                # Sort remaining columns based on their original indices
                remaining_cols.sort(key=lambda col: col_indices.get(col, 999))
            
            new_column_order = [district_col, 'Year'] + remaining_cols
            combined_df = combined_df[new_column_order]
        
        # Export to CSV
        csv_path = os.path.join(directory_path, output_csv)
        combined_df.to_csv(csv_path, index=False)
        print(f"Successfully created CSV: {csv_path}")
        
        # Export to Parquet
        parquet_path = os.path.join(directory_path, output_parquet)
        combined_df.to_parquet(parquet_path, index=False)
        print(f"Successfully created Parquet: {parquet_path}")
        
        print(f"Combined {len(dfs)} Excel files with {len(combined_df)} total rows")
        print(f"Final columns: {', '.join(combined_df.columns)}")
        
        # Print data types for verification
        print("\nData types in final dataset:")
        for col, dtype in combined_df.dtypes.items():
            print(f"{col}: {dtype}")
    else:
        print("No Excel files were successfully processed")

In [25]:
data_folder = "/fsx/avijit/projects/datacommonsMA/mcas_results"
combine_excel_files(data_folder)

Preview of first file (/fsx/avijit/projects/datacommonsMA/mcas_results/NextGenMCAS_2018.xlsx):
                                                  0              1        2   \
0     2018 Next Generation MCAS Achievement Results             NaN      NaN   
1                                      District Name  District Code  Subject   
2       Abby Kelley Foster Charter Public (District)       04450000      ELA   
3       Abby Kelley Foster Charter Public (District)       04450000     MATH   
4                                           Abington       00010000      ELA   
5                                           Abington       00010000     MATH   
6  Academy Of the Pacific Rim Charter Public (Dis...       04120000      ELA   
7  Academy Of the Pacific Rim Charter Public (Dis...       04120000     MATH   
8                                   Acton-Boxborough       06000000      ELA   
9                                   Acton-Boxborough       06000000     MATH   

             3      4   

/tmp/ipykernel_2144425/3133257492.py:108: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  combined_df = pd.concat(dfs, ignore_index=True)


Removing 0 possible header rows
Successfully created CSV: /fsx/avijit/projects/datacommonsMA/mcas_results/combined_mcas_data.csv
Successfully created Parquet: /fsx/avijit/projects/datacommonsMA/mcas_results/combined_mcas_data.parquet
Combined 8 Excel files with 6741 total rows
Final columns: District Name, Year, District Code, Subject, M+E #, M+E %, E #, E %, M #, M %, PM #, PM %, NM #, NM %, No. of Students Included, Avg. Scaled Score, SGP, Included In SGP

Data types in final dataset:
District Name: object
Year: object
District Code: object
Subject: object
M+E #: float64
M+E %: int64
E #: float64
E %: int64
M #: float64
M %: int64
PM #: float64
PM %: int64
NM #: float64
NM %: int64
No. of Students Included: float64
Avg. Scaled Score: float64
SGP: float64
Included In SGP: float64
